#  <u>*Final Task : Pepper Pirate Paradise Ltd. Analysis .*</u>

## <u>*Analysis objective*</u>
### <u>*To predict and forecast the selling prices of Bell Peppers of different colors (green, red, yellow)*</u>

#### *Importing essintial Libraries*

In [21]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
%matplotlib inline
import matplotlib
matplotlib.rcParams["figure.figsize"]=(20,10)
import seaborn as sns;sns.set()
import warnings
warnings.filterwarnings('ignore')
import plotly.express as px
from datetime import datetime,time

## *A.* <u>*Importing data*</u>

In [22]:
df=pd.read_csv(r"C:\Users\Omar\Desktop\SiTeck\Month_1\Final_Project_data\actual_data.csv")
df.head()

week_start_dt week_end_dt  vietnam_season p_color     price  total_volume  \
0    2015-08-17  2015-08-23               1  yellow  7.249725          -1.0   
1    2015-08-17  2015-08-23               1     red  7.600215          -1.0   
2    2015-08-17  2015-08-23               1   green  7.074805          -1.0   
3    2015-08-24  2015-08-30               1   green  7.025085          -1.0   
4    2015-08-24  2015-08-30               1     red  7.722255          -1.0   

   brazil  india  vietnam  indonesia  china  brazil_season  indonesia_season  \
0    -1.0   -1.0     -1.0       -1.0   -1.0           True              True   
1    -1.0   -1.0     -1.0       -1.0   -1.0           True              True   
2    -1.0   -1.0     -1.0       -1.0   -1.0           True              True   
3    -1.0   -1.0     -1.0       -1.0   -1.0           True              True   
4    -1.0   -1.0     -1.0       -1.0   -1.0           True              True   

   india_season  china_season  jordan_max_price  jordan_min_price  demand  \
0          True          True             7.425             7.025     0.5   
1          True          True             8.125             7.825     0.5   
2          True          True             7.525             7.225     0.5   
3          True          True             7.425             7.225     0.5   
4          True          True             8.125             7.825     0.5   

   supply  
0     0.5  
1     0.5  
2     0.5  
3     0.5  
4     0.5

In [23]:
df2=pd.read_csv(r"C:\Users\Omar\Desktop\SiTeck\Month_1\Final_Project_data\projection_outside_supply.csv")
df2

week_end_dt   brazil  india    vietnam  indonesia    china  brazil_season  \
0  2023-10-08  62609.9      0  2365023.5    27739.8   8678.3          False   
1  2023-10-15  22744.0      0  2345998.8    15052.6   6508.7          False   
2  2023-10-22  10961.5      0  2555267.6        0.0  15187.1          False   
3  2023-10-29   9211.5      0  2530537.9        0.0  15187.1          False   

   indonesia_season  india_season  china_season  total_volume  
0             False          True         False     2464051.7  
1             False          True         False     2390304.2  
2             False          True         False     2581416.4  
3             False          True         False     2554936.6

## *B.* <u>*Data shape*</u>

In [24]:
df.shape

(1272, 19)

In [25]:
df2.shape

(4, 11)

## *C.* <u>*Data info*</u>

In [26]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1272 entries, 0 to 1271
Data columns (total 19 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   week_start_dt     1272 non-null   object 
 1   week_end_dt       1272 non-null   object 
 2   vietnam_season    1272 non-null   int64  
 3   p_color           1272 non-null   object 
 4   price             1272 non-null   float64
 5   total_volume      1272 non-null   float64
 6   brazil            1272 non-null   float64
 7   india             1272 non-null   float64
 8   vietnam           1272 non-null   float64
 9   indonesia         1272 non-null   float64
 10  china             1272 non-null   float64
 11  brazil_season     1272 non-null   bool   
 12  indonesia_season  1272 non-null   bool   
 13  india_season      1272 non-null   bool   
 14  china_season      1272 non-null   bool   
 15  jordan_max_price  1241 non-null   float64
 16  jordan_min_price  1241 non-null   float64


---

##  *D.* <u>*Data Cleaning*</u>

### *D.1 na-values*
*for the Null values in the features (jordan_max_price & jordan_min_price) we decided to replace it using the interpolation function as below*

In [27]:
df.interpolate(method="linear",inplace=True,limit_direction="backward")

*Considered the 1st 56 rows as null values and drop it from the model as the numbers of volums are not helpfull*

In [28]:
df.drop(index=df.index[0:57],axis=0,inplace=True)

---

## *E. <u>Data Transformation*</u>

*Transform the feature "vietnam_season" to str in order to apply one hot encoding later*

In [29]:
df["vietnam_season"]=df["vietnam_season"].astype("str")

*Replacing the values [True,Fales] with 1,0 ,where 1 is True & 0 is False*

In [30]:
for col in df:
    if col in ["brazil_season","indonesia_season","india_season","china_season"]:
        df[col]=df[col].apply(lambda x:1 if x is True else 0)

*Applying one hot encoding the the features ["vietnam_season","p_color"]:*

In [31]:
for col in df:
    if col in ["vietnam_season","p_color"]:        
        one_hot_encoded_data = pd.get_dummies(df[col])
        one_hot_encoded_data=one_hot_encoded_data.applymap(lambda x:1 if x is True else 0 )
        df=pd.concat([df.drop([col],axis=1),one_hot_encoded_data],axis=1)
        df.rename(columns={"1":"vietnam_season_1","2":"vietnam_season_2","3":"vietnam_season_3"},inplace=True)

In [32]:
from datetime import datetime,timedelta
future_date_index=pd.date_range(start="2023-10-08",end="2023-10-29",freq="W")
future_date=pd.DataFrame({"date":future_date_index}).set_index("date")

*Concatenate the two data sets in one*

In [33]:
df=pd.concat([df,df2],axis=0)
df

week_start_dt week_end_dt     price  total_volume   brazil    india  \
57      2015-12-28  2016-01-03  6.599075     1596040.2  10793.5  65658.1   
58      2015-12-28  2016-01-03  7.175335     1596040.2  10793.5  65658.1   
59      2015-12-28  2016-01-03  7.300575     1596040.2  10793.5  65658.1   
60      2016-01-04  2016-01-10  7.379675     2295578.0   5677.8  15274.4   
61      2016-01-04  2016-01-10  7.175335     2295578.0   5677.8  15274.4   
...            ...         ...       ...           ...      ...      ...   
1271    2023-09-25  2023-10-01  8.758362     2665343.9    167.8  45376.1   
0              NaN  2023-10-08       NaN     2464051.7  62609.9      0.0   
1              NaN  2023-10-15       NaN     2390304.2  22744.0      0.0   
2              NaN  2023-10-22       NaN     2581416.4  10961.5      0.0   
3              NaN  2023-10-29       NaN     2554936.6   9211.5      0.0   

        vietnam  indonesia    china  brazil_season  ...  jordan_max_price  \
57    1519588.5        0.0      0.0              0  ...             6.625   
58    1519588.5        0.0      0.0              0  ...             7.525   
59    1519588.5        0.0      0.0              0  ...             7.425   
60    2274625.7        0.0      0.0              0  ...             7.525   
61    2274625.7        0.0      0.0              0  ...             7.625   
...         ...        ...      ...            ...  ...               ...   
1271  2521054.0    78334.2   8618.2              0  ...             9.625   
0     2365023.5    27739.8   8678.3              0  ...               NaN   
1     2345998.8    15052.6   6508.7              0  ...               NaN   
2     2555267.6        0.0  15187.1              0  ...               NaN   
3     2530537.9        0.0  15187.1              0  ...               NaN   

      jordan_min_price  demand      supply  vietnam_season_1  \
57               6.325    0.50    0.500000               0.0   
58               7.125    0.51    0.500000               0.0   
59               7.025   16.55    0.500000               0.0   
60               7.025  271.16    0.500000               0.0   
61               7.125   42.33    0.500000               0.0   
...                ...     ...         ...               ...   
1271             8.825  409.19  196.703982               1.0   
0                  NaN     NaN         NaN               NaN   
1                  NaN     NaN         NaN               NaN   
2                  NaN     NaN         NaN               NaN   
3                  NaN     NaN         NaN               NaN   

      vietnam_season_2  vietnam_season_3  green  red  yellow  
57                 1.0               0.0    1.0  0.0     0.0  
58                 1.0               0.0    0.0  1.0     0.0  
59                 1.0               0.0    0.0  0.0     1.0  
60                 1.0               0.0    0.0  0.0     1.0  
61                 1.0               0.0    0.0  1.0     0.0  
...                ...               ...    ...  ...     ...  
1271               0.0               0.0    0.0  0.0     1.0  
0                  NaN               NaN    NaN  NaN     NaN  
1                  NaN               NaN    NaN  NaN     NaN  
2                  NaN               NaN    NaN  NaN     NaN  
3                  NaN               NaN    NaN  NaN     NaN  

[1219 rows x 23 columns]

*Droppring the feature "week_start_dt"*

In [34]:
df.drop('week_start_dt',axis=1,inplace=True)

*Transform the feature "week_end_dt" to date type and extract Year,Month*

In [35]:
for col in df:
    if col in ["week_end_dt"]:
        df[col]=pd.to_datetime(df[col])
        df["year"]=df[col].dt.year
        df["month"]=df[col].dt.month

*Set the Feature "week_end_dt" as index*

In [36]:
df.set_index("week_end_dt",inplace=True)

In [37]:
df

price  total_volume   brazil    india    vietnam  indonesia  \
week_end_dt                                                                   
2016-01-03   6.599075     1596040.2  10793.5  65658.1  1519588.5        0.0   
2016-01-03   7.175335     1596040.2  10793.5  65658.1  1519588.5        0.0   
2016-01-03   7.300575     1596040.2  10793.5  65658.1  1519588.5        0.0   
2016-01-10   7.379675     2295578.0   5677.8  15274.4  2274625.7        0.0   
2016-01-10   7.175335     2295578.0   5677.8  15274.4  2274625.7        0.0   
...               ...           ...      ...      ...        ...        ...   
2023-10-01   8.758362     2665343.9    167.8  45376.1  2521054.0    78334.2   
2023-10-08        NaN     2464051.7  62609.9      0.0  2365023.5    27739.8   
2023-10-15        NaN     2390304.2  22744.0      0.0  2345998.8    15052.6   
2023-10-22        NaN     2581416.4  10961.5      0.0  2555267.6        0.0   
2023-10-29        NaN     2554936.6   9211.5      0.0  2530537.9        0.0   

               china  brazil_season  indonesia_season  india_season  ...  \
week_end_dt                                                          ...   
2016-01-03       0.0              0                 0             0  ...   
2016-01-03       0.0              0                 0             0  ...   
2016-01-03       0.0              0                 0             0  ...   
2016-01-10       0.0              0                 0             0  ...   
2016-01-10       0.0              0                 0             0  ...   
...              ...            ...               ...           ...  ...   
2023-10-01    8618.2              0                 0             1  ...   
2023-10-08    8678.3              0                 0             1  ...   
2023-10-15    6508.7              0                 0             1  ...   
2023-10-22   15187.1              0                 0             1  ...   
2023-10-29   15187.1              0                 0             1  ...   

             demand      supply  vietnam_season_1  vietnam_season_2  \
week_end_dt                                                           
2016-01-03     0.50    0.500000               0.0               1.0   
2016-01-03     0.51    0.500000               0.0               1.0   
2016-01-03    16.55    0.500000               0.0               1.0   
2016-01-10   271.16    0.500000               0.0               1.0   
2016-01-10    42.33    0.500000               0.0               1.0   
...             ...         ...               ...               ...   
2023-10-01   409.19  196.703982               1.0               0.0   
2023-10-08      NaN         NaN               NaN               NaN   
2023-10-15      NaN         NaN               NaN               NaN   
2023-10-22      NaN         NaN               NaN               NaN   
2023-10-29      NaN         NaN               NaN               NaN   

             vietnam_season_3  green  red  yellow  year  month  
week_end_dt                                                     
2016-01-03                0.0    1.0  0.0     0.0  2016      1  
2016-01-03                0.0    0.0  1.0     0.0  2016      1  
2016-01-03                0.0    0.0  0.0     1.0  2016      1  
2016-01-10                0.0    0.0  0.0     1.0  2016      1  
2016-01-10                0.0    0.0  1.0     0.0  2016      1  
...                       ...    ...  ...     ...   ...    ...  
2023-10-01                0.0    0.0  0.0     1.0  2023     10  
2023-10-08                NaN    NaN  NaN     NaN  2023     10  
2023-10-15                NaN    NaN  NaN     NaN  2023     10  
2023-10-22                NaN    NaN  NaN     NaN  2023     10  
2023-10-29                NaN    NaN  NaN     NaN  2023     10  

[1219 rows x 23 columns]

*Replace the new null values with the 0*

In [38]:
df.fillna(0,inplace=True)

In [39]:
df

price  total_volume   brazil    india    vietnam  indonesia  \
week_end_dt                                                                   
2016-01-03   6.599075     1596040.2  10793.5  65658.1  1519588.5        0.0   
2016-01-03   7.175335     1596040.2  10793.5  65658.1  1519588.5        0.0   
2016-01-03   7.300575     1596040.2  10793.5  65658.1  1519588.5        0.0   
2016-01-10   7.379675     2295578.0   5677.8  15274.4  2274625.7        0.0   
2016-01-10   7.175335     2295578.0   5677.8  15274.4  2274625.7        0.0   
...               ...           ...      ...      ...        ...        ...   
2023-10-01   8.758362     2665343.9    167.8  45376.1  2521054.0    78334.2   
2023-10-08   0.000000     2464051.7  62609.9      0.0  2365023.5    27739.8   
2023-10-15   0.000000     2390304.2  22744.0      0.0  2345998.8    15052.6   
2023-10-22   0.000000     2581416.4  10961.5      0.0  2555267.6        0.0   
2023-10-29   0.000000     2554936.6   9211.5      0.0  2530537.9        0.0   

               china  brazil_season  indonesia_season  india_season  ...  \
week_end_dt                                                          ...   
2016-01-03       0.0              0                 0             0  ...   
2016-01-03       0.0              0                 0             0  ...   
2016-01-03       0.0              0                 0             0  ...   
2016-01-10       0.0              0                 0             0  ...   
2016-01-10       0.0              0                 0             0  ...   
...              ...            ...               ...           ...  ...   
2023-10-01    8618.2              0                 0             1  ...   
2023-10-08    8678.3              0                 0             1  ...   
2023-10-15    6508.7              0                 0             1  ...   
2023-10-22   15187.1              0                 0             1  ...   
2023-10-29   15187.1              0                 0             1  ...   

             demand      supply  vietnam_season_1  vietnam_season_2  \
week_end_dt                                                           
2016-01-03     0.50    0.500000               0.0               1.0   
2016-01-03     0.51    0.500000               0.0               1.0   
2016-01-03    16.55    0.500000               0.0               1.0   
2016-01-10   271.16    0.500000               0.0               1.0   
2016-01-10    42.33    0.500000               0.0               1.0   
...             ...         ...               ...               ...   
2023-10-01   409.19  196.703982               1.0               0.0   
2023-10-08     0.00    0.000000               0.0               0.0   
2023-10-15     0.00    0.000000               0.0               0.0   
2023-10-22     0.00    0.000000               0.0               0.0   
2023-10-29     0.00    0.000000               0.0               0.0   

             vietnam_season_3  green  red  yellow  year  month  
week_end_dt                                                     
2016-01-03                0.0    1.0  0.0     0.0  2016      1  
2016-01-03                0.0    0.0  1.0     0.0  2016      1  
2016-01-03                0.0    0.0  0.0     1.0  2016      1  
2016-01-10                0.0    0.0  0.0     1.0  2016      1  
2016-01-10                0.0    0.0  1.0     0.0  2016      1  
...                       ...    ...  ...     ...   ...    ...  
2023-10-01                0.0    0.0  0.0     1.0  2023     10  
2023-10-08                0.0    0.0  0.0     0.0  2023     10  
2023-10-15                0.0    0.0  0.0     0.0  2023     10  
2023-10-22                0.0    0.0  0.0     0.0  2023     10  
2023-10-29                0.0    0.0  0.0     0.0  2023     10  

[1219 rows x 23 columns]

##  *f.* <u>*Data describtion*</u>

*Fom the below table We can notice that :*<br>
*1. the price,total_volume,vietnam mean and median are almos the same -->normaly distributed*<br>
*2. jordan_max_price & jordan_min_price are little right skeweded*<br>
*3. other numeric features are highly right skeweded*

In [50]:
pd.DataFrame(df.describe().T)

count          mean            std       min           25%  \
price             1219.0  7.982521e+00       1.440065       0.0  6.999910e+00   
total_volume      1219.0  2.245531e+06  481458.044606  325471.0  1.938246e+06   
brazil            1219.0  2.445847e+05  238473.305708       0.0  1.060860e+04   
india             1219.0  2.864978e+04   55837.161901       0.0  0.000000e+00   
vietnam           1219.0  1.808638e+06  574091.899609  220121.5  1.402234e+06   
indonesia         1219.0  1.544747e+05  242983.642750       0.0  0.000000e+00   
china             1219.0  8.497170e+03   21332.729934       0.0  0.000000e+00   
brazil_season     1219.0  4.306809e-01       0.495375       0.0  0.000000e+00   
indonesia_season  1219.0  2.559475e-01       0.436572       0.0  0.000000e+00   
india_season      1219.0  2.518458e-01       0.434251       0.0  0.000000e+00   
china_season      1219.0  3.396226e-01       0.473776       0.0  0.000000e+00   
jordan_max_price  1219.0  8.481481e+00       1.569245       0.0  7.425000e+00   
jordan_min_price  1219.0  7.900656e+00       1.438932       0.0  6.925000e+00   
demand            1219.0  2.287598e+02     225.831286       0.0  7.519500e+01   
supply            1219.0  7.561849e+01     112.953714       0.0  5.000000e-01   
vietnam_season_1  1219.0  3.396226e-01       0.473776       0.0  0.000000e+00   
vietnam_season_2  1219.0  3.986874e-01       0.489829       0.0  0.000000e+00   
vietnam_season_3  1219.0  2.584085e-01       0.437939       0.0  0.000000e+00   
green             1219.0  3.322395e-01       0.471210       0.0  0.000000e+00   
red               1219.0  3.322395e-01       0.471210       0.0  0.000000e+00   
yellow            1219.0  3.322395e-01       0.471210       0.0  0.000000e+00   
year              1219.0  2.019402e+03       2.250166    2016.0  2.017000e+03   
month             1219.0  6.379820e+00       3.413143       1.0  3.000000e+00   

                           50%           75%           max  
price             7.600050e+00  8.600420e+00  1.408459e+01  
total_volume      2.258416e+06  2.544656e+06  3.555979e+06  
brazil            1.752764e+05  4.435506e+05  8.776478e+05  
india             0.000000e+00  3.102260e+04  3.489974e+05  
vietnam           1.785483e+06  2.218162e+06  3.549175e+06  
indonesia         2.150300e+03  2.784692e+05  1.061051e+06  
china             0.000000e+00  7.257400e+03  2.109202e+05  
brazil_season     0.000000e+00  1.000000e+00  1.000000e+00  
indonesia_season  0.000000e+00  1.000000e+00  1.000000e+00  
india_season      0.000000e+00  1.000000e+00  1.000000e+00  
china_season      0.000000e+00  1.000000e+00  1.000000e+00  
jordan_max_price  8.025000e+00  9.225000e+00  1.422500e+01  
jordan_min_price  7.525000e+00  8.525000e+00  1.372500e+01  
demand            1.174400e+02  3.908050e+02  1.342040e+03  
supply            3.569561e+01  7.846879e+01  6.166545e+02  
vietnam_season_1  0.000000e+00  1.000000e+00  1.000000e+00  
vietnam_season_2  0.000000e+00  1.000000e+00  1.000000e+00  
vietnam_season_3  0.000000e+00  1.000000e+00  1.000000e+00  
green             0.000000e+00  1.000000e+00  1.000000e+00  
red               0.000000e+00  1.000000e+00  1.000000e+00  
yellow            0.000000e+00  1.000000e+00  1.000000e+00  
year              2.019000e+03  2.021000e+03  2.023000e+03  
month             6.000000e+00  9.000000e+00  1.200000e+01

*Matrix plot -Considering the index as price feature*

In [49]:
import plotly.figure_factory as ff

figure = ff.create_scatterplotmatrix(
    df[['price','total_volume', 'brazil', 'india', 'vietnam', 'indonesia', 'china',
        'demand', 'supply']],
    height=1000,
    width=1450,
    diag='box',
    index='price')

figure.show()

*Correlation plot*

In [43]:
corrs = df[['price','total_volume', 'brazil', 'india', 'vietnam', 'indonesia', 'china',
        'demand', 'supply']].corr()

figure = ff.create_annotated_heatmap(
    z=corrs.values,
    x=list(corrs.columns),
    y=list(corrs.index),
    colorscale='Earth',
    annotation_text=corrs.round(2).values,
    showscale=True, reversescale=True)
figure.show()